# Task 1 (Detecting pathological gamblers)

### paths

In [1]:
TASK1_TRAINING_PATH = "../../task1/training/t1_training/TRAINING_DATA/2021_cases/data/"
TASK1_GOLDENTRUTH_PATH = "../../task1/training/t1_training/TRAINING_DATA/2021_cases/risk_golden_truth.txt"
P_FILE = "../posts.csv"
TOKEN_FILE = "../tokens.csv"
LANG_DETECTOR_PATH="../../fasttextlanguagedetection.bin"
POSTS_GATHERED=False


### extracting subjects and respective classes

In [2]:
def get_golden_truth(path):
    labels={}
    with open(path, "r") as f:
        for line in f:
            splt_line = line.split(' ')
            labels[splt_line[0][7:]]=int(splt_line[1])
    return labels

In [3]:
if not POSTS_GATHERED:
    subject_labels=get_golden_truth(TASK1_GOLDENTRUTH_PATH)
    subject_labels

In [4]:
#without bf
import xml.etree.ElementTree as ET

def get_data(filename):
    tree = ET.parse(filename + ".xml")
  
    
    root = tree.getroot()
    
    writings = []
    for w in root.findall('WRITING'):
        #print(w)
        date = w.find('DATE').text
        if not date:
            date='\"\"'
        
        title = w.find('TITLE').text
        if not title:
            title=""
        else:
            title=title.replace("\n"," ")
            title=title.replace("\"","\'")
        text = w.find('TEXT').text
        if not text:
            text=""
        else:
            text=text.replace("\n"," ")
            text=text.replace("\"","\'")
        writings.append((date,title,text))
    return writings

In [5]:
#debugging particular users
testing_s = ['945']
for s in testing_s:
    d=get_data(TASK1_TRAINING_PATH  +'subject'+ s)
    print(d[58])
    #for w in d:
    #    print(w[1])


('2018-09-08 02:28:47', "'...set fire to every major U.S. city and have our Communist forces launch their attack while Silicon Valley sits in their bunkers in the middle of the pacific ocean in New Zealand! #8221; Alex Jones' plea for sanity", "Alex Jones is taking his ban from social media in stride as he dons a donkey mask and 'speaks truth to power' with these great words of wisdom on what he calls 'operation 666':  #8220;On the sixth of August we banned Infowars on 27 platforms! #8221; he screeches.  #8220;And now on September sixth we banned you from Twitter! And on October sixth, we will destroy your president and set fire to every major U.S. city and have our Communist forces launch their attack while Silicon Valley sits in their bunkers in the middle of the pacific ocean in New Zealand! #8221; https://news.avclub.com/lets-check-in-on-alex-jones-who-is-not-handling-his-tw-1828894038/amp")


### Cleaning the text

In [6]:
import re
import nltk

from nltk.tokenize import sent_tokenize
#from nltk.corpus import wordnet
import string

translate_table = dict((ord(char), ' ') for char in string.punctuation if not char in ['!','.','?',',']) 


In [7]:
string.punctuation

'!"#$%&\'()*+,-./:;<=>?@[\\]^_`{|}~'

In [8]:
import fasttext
import contractions #might test pycontractions later

lang_detector = fasttext.load_model(LANG_DETECTOR_PATH)
slang_dict = {
    'thx':'thanks',
    'ty':'thank you',
    'eli':'explain like i am', #not eli5 since the number gets preprocessed prior to this step
    'gg':'good game',
    'gj':'good job',
    'gl':'good luck',
    'ff':'forfeit',
    'oc':'original content',
    'ama':'ask me anything',
    'aka':'also known as',
    'ikr':'i know right',
    'iirc':'if i recall correctly',
    'lol':'laughing out loud',
    'pls':'please',
    'nsfw':'not safe for work',
    'nsfl':'not safe for life',
    'omg':'oh my god',
    'omfg':'oh my fucking god',
    'lmao':'laughing my ass off',
    'lmfao':'laughing my fucking ass off',
    'af':'as fuck',
    'lpt':'life pro tip',
    'imo':'in my opinion',
    'dat':'that',
    'np':'no problem',
    'fml':'fuck my life',
    'wtf':'what the fuck',
    'wat':'what',
    'wot':'what',
    'wut':'what',
    'imho':'in my honest opinion',
    'fb':'facebook',
    'ft':'featuring',
    'vs':'versus',
    'fyi':'for your information',
    'asap':'as soon as possible',
    'g2g':'got to go',
    'ttyl':'talk to you later',
    'ftw':'for the win',
    'idc':'i don\'t care',
    'jk':'just kidding',
    'tfw':'that feeling when',
    'irl':'in real life',
    'btw':'by the way',
    'tldr':'too long did not read',
    'tl dr':'too long did not read',
    'dw':'do not worry',
    'yolo':'you only live once',
    'tmi':'too much information',
    'rip':'rest in peace'
}
for abv in slang_dict:
    contractions.add(abv,slang_dict[abv])

def cleaning(text):
    text = text.lower()
    text = re.sub(r" #821[67];", "\'", text) #apostrophe character
    text = re.sub(r" amp;", "&", text) #ampersand character
    text = re.sub(r" lt;", "<", text) #html < character
    text = re.sub(r" gt;", ">", text) #html > character
    text = re.sub(r"[:=xX]\^?[)dD\]]", "smiling emoji", text) #common positive emojis
    text = re.sub(r"[:=]\^?[|\[(]", "negative emoji", text) #common negative emojis
    text = re.sub(r"D[:=]", "negative emoji", text) #other common negative emojis
    text = re.sub(r"https?://\S+|www\.\S+", "url", text) #url links
    text = re.sub(r'/?u/\S+/?',"user", text) #reddit user references
    text = re.sub(r'/?r/\S+/?',"subreddit", text) #subreddit references
    text = re.sub(r'\d+[,\.]\d+[$€]'," money ", text) #money references 
    text = re.sub(r'\d+[$€]'," money ", text) #money references
    text = re.sub(r'[$€]\d+[,\.]?\d*[kK]?'," money ", text) #money references
    text = re.sub(r' #\d+;',"", text) #convert rest of unicode
    text = re.sub(r'\d+[,\.]?\d*'," number ", text) #convert numbers #recheck
    #expand common contractions
    text = contractions.fix(text)
    #remove most punctuaction
    text = text.translate(translate_table)
    #remove extra whitespaces
    text = re.sub(r'\s+', ' ', text)
    text = text.strip()

    return text

def language_check(text):
    # add language checking
    ## should it be on post or sentence level?
    #try:
    langs = lang_detector.predict(text,k=2)[0]
    return langs


In [9]:
#example
cleaning("https://www.reddit.com/r/MachineLearning is pretty cool yall!!! OMG rated 9.9 out of 10 by /u/hello-dude :) would pay 5.50$ to meet the mods irl")

'url is pretty cool you all!!! oh my god rated number out of number by user smiling emoji would pay money to meet the mods in real life'

In [10]:
cleaning("17 with low self esteem. honest opinions please.")


'number with low self esteem. honest opinions please.'

### building single file dataset

In [11]:
from io import BytesIO
from csv import writer
total_posts=0
non_english_posts=0
langs_detected={}

if not POSTS_GATHERED:
    with open(P_FILE, "w",encoding="utf-8") as f:
        output = BytesIO()
        csv_writer = writer(f, delimiter='\t')
        
        
        header = ["User","Post_Nr", "Date", "Title", "Post", "Cleaned_Sentences", "Label"]
        csv_writer.writerow(header)
        for subject in subject_labels:
        #for subject in subject_labels:    
            text_data = get_data(TASK1_TRAINING_PATH  +'subject'+ subject)
            i=0
            for  post in text_data:
                total_posts+=1
                if post[1]!='' and post[2]=='':
                    cleaned_text = cleaning(post[1])
                    
                elif  post[1]=='' and post[2]!='':
                    cleaned_text = cleaning(post[2])

                elif post[1]!='' and post[2]!='': #needed due to bug with subject6321
                    cleaned_text = cleaning(post[1]) + " " + cleaning(post[2])

                else:
                    continue
                
                langs = language_check(cleaned_text)
                #checking if its in english and if it contains letters
                if '__label__en' in langs and re.search('[a-zA-Z]',cleaned_text)!=None:
                    row = [subject, i, post[0], post[1], post[2], cleaned_text, subject_labels[subject]]
                    csv_writer.writerow(row)
                    i+=1
                else:
                    
                    print(langs,cleaned_text)
                    for lang in langs:
                        langs_detected[lang] = langs_detected.get(lang,0)+1
                    
                    non_english_posts+=1
        output.seek(0)

    with open("dataset_stats.txt","w") as stats_f:
        stats_f.write(f"Went through {total_posts} total posts, {non_english_posts} of which were discarded due to not being in english\n")
        stats_f.write("languages found:\n")
        for lang in langs_detected:
            stats_f.write(f"{lang}: {langs_detected[lang]}\n")
    print(f"Went through {total_posts} total posts, {non_english_posts} of which were discarded due to not being in english")


('__label__pt', '__label__gl') no
('__label__nl', '__label__ca') beaut!!!
('__label__kn', '__label__tt') use a vpn.
('__label__eo', '__label__es') mi estas el nov zelando smiling emoji!
('__label__eo', '__label__tr') you ekzistas ia piratajn librojn en esperanto? mi volas legi libron pri piratoj! se vi scias, tiam bonvolu diri al mi. dankon kaj felicxan kristnaskon!
('__label__eo', '__label__de') dankon smiling emoji
('__label__eo', '__label__nl') kiel vi scias ke vi ne atas timigajn filmojn, se vi neniam spektis tian filmon
('__label__eo', '__label__nl') mi ege atas kafon! mi kutime trinkas tason da nigra kafo iumatene. teon anka plaas al mi, sed vere mi nur trinkas pipromentan teon
('__label__eo', '__label__uz') you tiuj afganaj homoj estis aktiva en la e movado? mojosa bildo! smiling emoji
('__label__eo', '__label__pl') mi atis i tiun libron kiam mi estis knabo. sed nun, tute ne! url fek al vi simon eliot
('__label__eo', '__label__nl') alkoholajxon? vi ricevas tion en botelo j haha


### opening resulting dataset with pandas

In [12]:
import pandas as pd
df = pd.read_csv(P_FILE, delimiter="\t")#,converters={"Cleaned_Sentences": literal_eval})

#df['Cleaned_Text'] = df['Cleaned_Text'].apply(ast.literal_eval)
#df = df.dropna(subset=['Tokens'])
df

User  Post_Nr                 Date  \
0        3450        0  2018-01-03 19:59:34   
1        3450        1  2018-01-07 17:33:14   
2        3450        2  2018-01-07 18:08:21   
3        3450        3  2018-01-14 21:54:10   
4        3450        4  2018-01-15 08:40:46   
...       ...      ...                  ...   
1071857  6377       22  2020-10-03 12:55:24   
1071858  6377       23  2020-10-10 01:45:51   
1071859  6377       24  2020-10-12 06:45:36   
1071860  6377       25  2020-10-12 06:53:24   
1071861  6377       26  2020-10-12 08:44:37   

                                                     Title  \
0        Sports betting: -4.5k in debt, feeling very de...   
1            Finally accepted that you cannot win gambling   
2                            Blocking software - betfilter   
3                           Prone to relapse when in debt?   
4                       Down to my last 100 on credit card   
...                                                    ...   
1071857  MOLTRES RAID 10 PEOPLE 4666 3889 9100 AND 7979...   
1071858                                                NaN   
1071859                           Sudowoodo 4666 3889 9100   
1071860                                                NaN   
1071861                  Sudowoodo raid now 4666 3889 9100   

                                                      Post  \
0        I am currently in the red by -4.5k. To summari...   
1        Relapsed, had a last flurry thinking that I co...   
2        Has anybody used this, what were your experien...   
3        I find that when in debt I am more likely to r...   
4        I am -4.6k in debt, I have stopped gambling bu...   
...                                                    ...   
1071857                                                NaN   
1071858                               4666-3889-9100 lv 36   
1071859                                                NaN   
1071860                                I like it shiny tho   
1071861                                                NaN   

                                         Cleaned_Sentences  Label  
0        sports betting number k in debt, feeling very ...      1  
1        finally accepted that you cannot win gambling ...      1  
2        blocking software betfilter has anybody used t...      1  
3        prone to relapse when in debt? i find that whe...      1  
4        down to my last number on credit card i am num...      1  
...                                                    ...    ...  
1071857  moltres raid number people number number numbe...      0  
1071858                     number number number lv number      0  
1071859                     sudowoodo number number number      0  
1071860                                i like it shiny tho      0  
1071861            sudowoodo raid now number number number      0  

[1071862 rows x 7 columns]

In [13]:
#debugging specific user
df[df['User']==945]

User  Post_Nr                 Date  \
202203   945        0  2016-04-16 18:53:28   
202204   945        1  2016-04-23 02:42:44   
202205   945        2  2016-04-25 03:54:05   
202206   945        3  2016-04-28 22:31:04   
202207   945        4  2016-05-01 16:52:38   
...      ...      ...                  ...   
203400   945     1197  2020-10-13 13:58:47   
203401   945     1198  2020-10-13 14:29:05   
203402   945     1199  2020-10-13 14:52:32   
203403   945     1200  2020-10-13 15:10:23   
203404   945     1201  2020-10-13 15:25:07   

                                                    Title  \
202203         Sargon still believes in cultural marxism.   
202204  'The fundamental realization that liberalism i...   
202205  'Perhaps Sargon and the Islamic Republic of Ir...   
202206  Nimrod of Akkad is here to free us from the il...   
202207  'Say what you will about GG but at least we di...   
...                                                   ...   
203400                                                NaN   
203401                                                NaN   
203402  Top Minds- Proud Boys Can't be Racists Because...   
203403                                                NaN   
203404                                                NaN   

                                                     Post  \
202203  In Sargon #8217;s latest video, 'Marxism, Femi...   
202204  This is the new 'white fragility'. Over privil...   
202205  I didn't want to make another post about Carl ...   
202206  https://www.youtube.com/watch?v=1o4CMasaLfQ Ni...   
202207  You know, I check this subreddit nearly daily....   
...                                                   ...   
203400   gt;the media are silent about Trump supporter...   
203401  Conservatives and their allies are always tryi...   
203402                                                NaN   
203403   gt;''If the Supreme Court says that you have ...   
203404  When have communists called for ethnic cleansi...   

                                        Cleaned_Sentences  Label  
202203  sargon still believes in cultural marxism. in ...      0  
202204  the fundamental realization that liberalism is...      0  
202205  perhaps sargon and the islamic republic of ira...      0  
202206  nimrod of akkad is here to free us from the il...      0  
202207  say what you will about good game but at least...      0  
...                                                   ...    ...  
203400  the media are silent about trump supporters .....      0  
203401  conservatives and their allies are always tryi...      0  
203402  top minds proud boys cannot be racists because...      0  
203403  if the supreme court says that you have the ri...      0  
203404  when have communists called for ethnic cleansi...      0  

[1202 rows x 7 columns]

### Tokenization

In [14]:
def tokenize_sentences(text):
    #if not '__label__en' in lang:
    #    return [],lang
        #raise Exception("Post is not considered to be in English")
    #except Exception:
    #    pass
            
    sentences = sent_tokenize(text)
    sentences = [sent for sent in sentences if sent!=' ']
    #text = re.sub(r'[^\x00-\x7f]',"", text) #non ascii
    #text = re.sub(r' #\d+;',"", text) #testing for now
    #text = re.sub(r"-", " ", text) #break hyphenated words
    #text = text.translate(translate_table) #remove punctuation
    
    return sentences
    

In [15]:
"""
from nltk.corpus import  wordnet
def get_wordnet_pos(treebank_tag):

    if treebank_tag.startswith('J'):
        return wordnet.ADJ
    elif treebank_tag.startswith('V'):
        return wordnet.VERB
    elif treebank_tag.startswith('N'):
        return wordnet.NOUN
    elif treebank_tag.startswith('R'):
        return wordnet.ADV
    else:
        return wordnet.NOUN #default
"""

"\nfrom nltk.corpus import  wordnet\ndef get_wordnet_pos(treebank_tag):\n\n    if treebank_tag.startswith('J'):\n        return wordnet.ADJ\n    elif treebank_tag.startswith('V'):\n        return wordnet.VERB\n    elif treebank_tag.startswith('N'):\n        return wordnet.NOUN\n    elif treebank_tag.startswith('R'):\n        return wordnet.ADV\n    else:\n        return wordnet.NOUN #default\n"

In [16]:
from nltk.tokenize import word_tokenize
from nltk.stem import SnowballStemmer
#from nltk.stem.wordnet import WordNetLemmatizer
#from nltk import pos_tag
import en_core_web_md
from spacy.lang.en import English

nlp=en_core_web_md.load(disable=['tok2vec','parser','senter','ner'])
ss = SnowballStemmer("english")
#wnl = WordNetLemmatizer()

def simplify(text, method=''):
    tokens=""
    
    if method=='stem':
        
        tokens = " ".join([ss.stem(tok) for tok in word_tokenize(text)])
        
    elif method=='lem':
        #sentences = tokenize_sentences(text)
        #for s in sentences:
        doc = nlp(text)
        tokens=" ".join([tok.lemma_ for tok in doc])
        #    tokens+=" ".join([wnl.lemmatize(token.text) for token in doc])
        #    tagged = pos_tag([token for token in word_tokenize(s)])
        #    tokens+=" ".join([wnl.lemmatize(token,get_wordnet_pos(pos)) for (token,pos) in tagged if not token in stop_words])
            
    
    return tokens

In [17]:
#tokens_df = df[['User', 'Post_Nr', 'Label']]

#tokens_df['Stem_Tokens'] = df['Cleaned_Sentences'].apply(lambda s: tokenize(s, method='stem'))
df['Stemmed'] = df['Cleaned_Sentences'].apply(lambda s: simplify(str(s), method='stem'))



df['Stemmed']

0          sport bet number k in debt , feel veri depress...
1          final accept that you can not win gambl relaps...
2          block softwar betfilt has anybodi use this , w...
3          prone to relaps when in debt ? i find that whe...
4          down to my last number on credit card i am num...
                                 ...                        
1071857    moltr raid number peopl number number number a...
1071858                       number number number lv number
1071859                       sudowoodo number number number
1071860                                  i like it shini tho
1071861              sudowoodo raid now number number number
Name: Stemmed, Length: 1071862, dtype: object

In [18]:
df['Lemmatized'] = df['Cleaned_Sentences'].apply(lambda s: simplify(str(s), method='lem'))



df['Lemmatized']

0          sports betting number k in debt , feeling very...
1          finally accepted that you can not win gambling...
2          blocking software betfilter has anybody used t...
3          prone to relapse when in debt ? i find that wh...
4          down to my last number on credit card i am num...
                                 ...                        
1071857    moltres raid number people number number numbe...
1071858                       number number number lv number
1071859                       sudowoodo number number number
1071860                                  i like it shiny tho
1071861              sudowoodo raid now number number number
Name: Lemmatized, Length: 1071862, dtype: object

In [19]:
df['Raw'] = df['Cleaned_Sentences']

In [20]:
columnsTitles = ['User', 'Post_Nr', 'Raw','Stemmed', 'Lemmatized', 'Label']
tokens_df = df[columnsTitles]
#tokens_df = tokens_df.reindex(columns=columnsTitles)
tokens_df.to_csv(TOKEN_FILE, sep='\t', index=False)

In [21]:
tokens_df

User  Post_Nr                                                Raw  \
0        3450        0  sports betting number k in debt, feeling very ...   
1        3450        1  finally accepted that you cannot win gambling ...   
2        3450        2  blocking software betfilter has anybody used t...   
3        3450        3  prone to relapse when in debt? i find that whe...   
4        3450        4  down to my last number on credit card i am num...   
...       ...      ...                                                ...   
1071857  6377       22  moltres raid number people number number numbe...   
1071858  6377       23                     number number number lv number   
1071859  6377       24                     sudowoodo number number number   
1071860  6377       25                                i like it shiny tho   
1071861  6377       26            sudowoodo raid now number number number   

                                                   Stemmed  \
0        sport bet number k in debt , feel veri depress...   
1        final accept that you can not win gambl relaps...   
2        block softwar betfilt has anybodi use this , w...   
3        prone to relaps when in debt ? i find that whe...   
4        down to my last number on credit card i am num...   
...                                                    ...   
1071857  moltr raid number peopl number number number a...   
1071858                     number number number lv number   
1071859                     sudowoodo number number number   
1071860                                i like it shini tho   
1071861            sudowoodo raid now number number number   

                                                Lemmatized  Label  
0        sports betting number k in debt , feeling very...      1  
1        finally accepted that you can not win gambling...      1  
2        blocking software betfilter has anybody used t...      1  
3        prone to relapse when in debt ? i find that wh...      1  
4        down to my last number on credit card i am num...      1  
...                                                    ...    ...  
1071857  moltres raid number people number number numbe...      0  
1071858                     number number number lv number      0  
1071859                     sudowoodo number number number      0  
1071860                                i like it shiny tho      0  
1071861            sudowoodo raid now number number number      0  

[1071862 rows x 6 columns]

In [22]:
tokens_df.isnull().sum()

User          0
Post_Nr       0
Raw           0
Stemmed       0
Lemmatized    0
Label         0
dtype: int64